In [1]:
#%run input/Format.ipynb
import ROOT as root
from array import array
root.gErrorIgnoreLevel = root.kFatal
%jsroot on
import numpy as np

In [2]:
file_path="/Users/mitrankova/Jupyter/PatternRecognition/input/"
#file_names=["0version_Box_TPC_Au_Au_ZeroField_1mrad_aligned_10evt_9nSkip_75570-0_resid.root"]
file_names=['Au_Au_seeds_37thevt_66522-0_resid.root']
#file_names=['Au_Au_seeds__8evts_7skip_75405-0_resid.root']

In [3]:
# Global mode: use radial triplets everywhere
TRIPLET_MODE = "radial"

def assert_radial():
    global TRIPLET_MODE
    if TRIPLET_MODE != "radial":
        print("Warning: Forcing TRIPLET_MODE='radial'")
        TRIPLET_MODE = "radial"

print("TRIPLET_MODE:", TRIPLET_MODE)


TRIPLET_MODE: radial


In [4]:
hists_read, hists_sim = [], []

# Open ROOT files and keep them open so TTrees remain accessible later
open_files = []  # keep TFile references alive
trees = {
    "cluster": [],
    "residual": [],
    "hit": [],
    "vertex": []
}

for iFile in range(len(file_names)):
    fpath = file_path + file_names[iFile]
    tfile = root.TFile.Open(fpath, "READ")
    if not tfile or tfile.IsZombie():
        print(f"Failed to open {fpath}")
        trees["cluster"].append(None)
        trees["residual"].append(None)
        trees["hit"].append(None)
        trees["vertex"].append(None)
        continue

    open_files.append(tfile)

    # Retrieve trees if available (names from your file structure)
    trees["cluster"].append(tfile.Get("clustertree"))
    trees["residual"].append(tfile.Get("residualtree"))
    trees["hit"].append(tfile.Get("hittree"))
    trees["vertex"].append(tfile.Get("vertextree"))

# Handy shorthand to the first file's trees
cluster_tree = trees["cluster"][0] if trees["cluster"] else None
residual_tree = trees["residual"][0] if trees["residual"] else None
hit_tree = trees["hit"][0] if trees["hit"] else None
vertex_tree = trees["vertex"][0] if trees["vertex"] else None

print(f"Loaded files: {len(open_files)}")
print("hit_tree entries:", hit_tree.GetEntries() if hit_tree else 0)
print("cluster_tree entries:", cluster_tree.GetEntries() if cluster_tree else 0)
print("residual_tree entries:", residual_tree.GetEntries() if residual_tree else 0)

Loaded files: 1
hit_tree entries: 93946
cluster_tree entries: 13109
residual_tree entries: 161


In [5]:
# Quick check: list a few branches from the trees so they are clearly accessible
if hit_tree:
    hit_branches = [hit_tree.GetListOfBranches().At(i).GetName() for i in range(min(100, hit_tree.GetListOfBranches().GetEntries()))]
    print("hit_tree branches (first 10):", hit_branches)
if cluster_tree:
    cluster_branches = [cluster_tree.GetListOfBranches().At(i).GetName() for i in range(min(10, cluster_tree.GetListOfBranches().GetEntries()))]
    print("cluster_tree branches (first 10):", cluster_branches)
if residual_tree:
    residual_branches = [residual_tree.GetListOfBranches().At(i).GetName() for i in range(min(10, residual_tree.GetListOfBranches().GetEntries()))]
    print("residual_tree branches (first 10):", residual_branches)

hit_tree branches (first 10): ['run', 'segment', 'event', 'gl1bco', 'hitsetkey', 'gx', 'gy', 'gz', 'layer', 'sector', 'side', 'stave', 'chip', 'strobe', 'ladderz', 'ladderphi', 'timebucket', 'pad', 'tbin', 'col', 'row', 'segtype', 'tile', 'strip', 'adc', 'zdriftlength', 'mbdcharge']
cluster_tree branches (first 10): ['run', 'segment', 'event', 'gl1bco', 'lx', 'lz', 'gx', 'gy', 'gz', 'phi']
residual_tree branches (first 10): ['run', 'segment', 'event', 'mbdcharge', 'mbdzvtx', 'firedTriggers', 'gl1BunchCrossing', 'trackid', 'tpcid', 'silid']


In [6]:
Npads = [94,128,192]
ADC_treshold_up = [20, 100, 1000000, 100000]
ADC_treshold_down = [0,  20, 60, 200  ]
Select_ADC_treshold = 2  # 0, 1, 2, 3

In [7]:
hists = {}

def get_hist(sector, imod, side):
    key = (sector, imod, side)
    if key in hists:
        return hists[key]

    hist = root.TH3F(
        f"hist3d_hard_sec{sector}_m{imod}_s{side}",
        f"3D ADC sec {sector} mod {imod} side {side}; timebin; pad; layer",
        300, 0,300,
        Npads[imod] , Npads[imod] * sector , Npads[imod] * (sector+1),
        16, 7 + 16*imod, 7 + 16*(imod + 1)
    )
    hists[key] = hist
    return hist

if hit_tree:
    n_entries = int(hit_tree.GetEntries())
    for entry in range(n_entries):
        hit_tree.GetEntry(entry)
        sector = int(hit_tree.sector)
        layer  = int(hit_tree.layer)
        imod   = (layer - 7) // 16
        if imod < 0 or imod > 2:
            continue

        side = int(hit_tree.side)
        #print( "Entry:", entry, "Layer:", layer, "Imod:", imod, "Side:", side , "Sector:", sector)
        if side not in (0, 1):
            continue

        
        #if side==0 and sector==0 and imod ==0 :
        #    print( hit_tree.adc)
        if(hit_tree.adc>ADC_treshold_down[Select_ADC_treshold]):
            get_hist(sector, imod, side).Fill( hit_tree.tbin, hit_tree.pad, layer, hit_tree.adc)
         #   print("Filled!")


In [8]:
'''draw_sector = 0
draw_side   = 0   # 0 or 1

canvases = []

# keep references to what you draw (important in PyROOT)
drawn = {}

for imod in range(3):
    c = root.TCanvas(
        f"c_sec{draw_sector}_s{draw_side}_mod{imod}",
        f"Sector {draw_sector} Side {draw_side} Module {imod}",
        900, 600
    )
    c.cd()

    key = (draw_sector, imod, draw_side)
    if key in hists:
        h3 = hists[key]  # TH3F
        h3.SetTitle(f"3D ADC; timebin; pad; layer  (sec {draw_sector}, side {draw_side}, mod {imod})")

        # Good TH3 draw options: "BOX2Z", "LEGO2Z", "ISO"
        # Try BOX2Z first (usually the clearest for occupancy/ADC maps)
        h3.GetXaxis().SetTitle("Time bin")
        h3.GetYaxis().SetTitle("Pad")
        h3.GetYaxis().SetTitleOffset(1.6)
        h3.GetZaxis().SetTitle("Layer")
        for ax in (h3.GetXaxis(), h3.GetYaxis(), h3.GetZaxis()):
            ax.SetTitleSize(0.045)
            ax.SetLabelSize(0.04)

        h3.Draw("SCAT")

        drawn[imod] = h3
   

    c.Update()
    canvases.append(c)

for c in canvases:
    c.Draw()'''


'draw_sector = 0\ndraw_side   = 0   # 0 or 1\n\ncanvases = []\n\n# keep references to what you draw (important in PyROOT)\ndrawn = {}\n\nfor imod in range(3):\n    c = root.TCanvas(\n        f"c_sec{draw_sector}_s{draw_side}_mod{imod}",\n        f"Sector {draw_sector} Side {draw_side} Module {imod}",\n        900, 600\n    )\n    c.cd()\n\n    key = (draw_sector, imod, draw_side)\n    if key in hists:\n        h3 = hists[key]  # TH3F\n        h3.SetTitle(f"3D ADC; timebin; pad; layer  (sec {draw_sector}, side {draw_side}, mod {imod})")\n\n        # Good TH3 draw options: "BOX2Z", "LEGO2Z", "ISO"\n        # Try BOX2Z first (usually the clearest for occupancy/ADC maps)\n        h3.GetXaxis().SetTitle("Time bin")\n        h3.GetYaxis().SetTitle("Pad")\n        h3.GetYaxis().SetTitleOffset(1.6)\n        h3.GetZaxis().SetTitle("Layer")\n        for ax in (h3.GetXaxis(), h3.GetYaxis(), h3.GetZaxis()):\n            ax.SetTitleSize(0.045)\n            ax.SetLabelSize(0.04)\n\n        h3.Draw("

In [9]:
hist3d_xyz = root.TH3F("hist3d_xyz", "3D ADC; x; y;z", 240, -60, 60, 240, -60, 60, 150,0, 150)
if hit_tree:
    for entry in range(hit_tree.GetEntries()):
        hit_tree.GetEntry(entry)
        x_hit = hit_tree.gx
        y_hit = hit_tree.gy
        z_hit = hit_tree.gz
        adc_hit = hit_tree.adc
        if (x_hit**2 + y_hit**2)**0.5 > 12:  # only fill if within 100 units
            hist3d_xyz.Fill(x_hit, y_hit, z_hit,adc_hit)


In [10]:
'''c1 = root.TCanvas("c1", "3D hits", 1200, 1000)
hist3d_xyz.Draw("colz")
c1.Draw()'''

'c1 = root.TCanvas("c1", "3D hits", 1200, 1000)\nhist3d_xyz.Draw("colz")\nc1.Draw()'

# Build Tree

In [11]:
import numpy as np
from collections import defaultdict
from scipy.spatial import cKDTree

# collect points per (sector, imod, side)
points = defaultdict(list)   # key -> list of (t, pad, layer)
payload = defaultdict(list)  # key -> list of (adc, entry)

if hit_tree:
    n_entries = int(hit_tree.GetEntries())
    for entry in range(n_entries):
        hit_tree.GetEntry(entry)

        sector = int(hit_tree.sector)
        layer  = int(hit_tree.layer)
        imod   = (layer - 7) // 16
        if imod < 0 or imod > 2:
            continue

        side = int(hit_tree.side)
        if side not in (0, 1):
            continue

        adc = int(hit_tree.adc)
        if  (adc < ADC_treshold_down[Select_ADC_treshold]):
            continue

        tbin = int(hit_tree.tbin)
        pad  = int(hit_tree.pad)

        key = (sector, imod, side)
        points[key].append((tbin, pad, layer))
        payload[key].append((adc, entry))
        used_global = set()
        if sector==0 and imod==0 and side==0:
            if layer==7 and tbin<30:
            #if tbin>10 and tbin<30 and pad>60 and pad<80 and layer>=7 and layer<8:
                print(f"Entry {entry}: tbin={tbin}, pad={pad}, layer={layer}, adc={adc}")
        

# build KD trees
kdtree = {}
pts_arr = {}
for key, pts in points.items():
    arr = np.asarray(pts, dtype=np.float32)
    pts_arr[key] = arr
    kdtree[key] = cKDTree(arr)

print("Built KD-trees:", len(kdtree))


Entry 3862: tbin=26, pad=56, layer=7, adc=112
Entry 3863: tbin=27, pad=56, layer=7, adc=65
Built KD-trees: 72


In [12]:
def box_query(key, tmin, tmax, pmin, pmax, lmin, lmax):
    tree = kdtree[key]
    arr  = pts_arr[key]

    # cheap preselect using a ball around the box center
    center = np.array([(tmin+tmax)/2.0, (pmin+pmax)/2.0, (lmin+lmax)/2.0], dtype=np.float32)
    half   = np.array([(tmax-tmin)/2.0, (pmax-pmin)/2.0, (lmax-lmin)/2.0], dtype=np.float32)
    radius = float(np.linalg.norm(half))  # ball that covers the whole box

    cand = tree.query_ball_point(center, r=radius)

    # exact box filter
    out = []
    for i in cand:
        t, p, l = arr[i]
        if (tmin <= t <= tmax) and (pmin <= p <= pmax) and (lmin <= l <= lmax):
            out.append(i)

    return out  # indices into payload[key]


In [13]:
def knn(key, t, p, l, k=10):
    d, idx = kdtree[key].query([t, p, l], k=k)
    return d, idx


In [14]:
key = (0, 0, 0)
idxs = box_query(key, tmin=10, tmax=30, pmin=50, pmax=60, lmin=7, lmax=7)

print(f"Box query found {len(idxs)} hits in key {key}:")

for i in idxs:
    tbin, pad, layer = pts_arr[key][i]
    adc, entry = payload[key][i]
    print(f"  Entry {entry}: tbin={int(tbin)}, pad={int(pad)}, layer={int(layer)}, adc={adc}")


Box query found 2 hits in key (0, 0, 0):
  Entry 3863: tbin=27, pad=56, layer=7, adc=65
  Entry 3862: tbin=26, pad=56, layer=7, adc=112


In [15]:
import numpy as np
from collections import defaultdict
from scipy.spatial import cKDTree

def build_layer_indices_and_trees(key, pts_arr, payload):
    """
    Input:
      pts_arr[key]  : Nx3 array (tbin, pad, layer)
      payload[key]  : list length N of (adc, entry)
    Output:
      layers[layer] = dict with:
         "idx": global indices of hits in this layer
         "tp" : Mx2 float array of (tbin,pad)
         "adc": M int array
         "tree": cKDTree on tp
    """
    arr = pts_arr[key]
    adcs = np.array([payload[key][i][0] for i in range(len(payload[key]))], dtype=np.int32)
    
    by_layer = defaultdict(list)
    for i in range(arr.shape[0]):
        layer = int(arr[i, 2])
        by_layer[layer].append(i)

    layers = {}
    for layer, idxs in by_layer.items():
        idxs = np.asarray(idxs, dtype=np.int32)
        tp = arr[idxs][:, :2].astype(np.int32)  # (tbin, pad) as integers
        adc = adcs[idxs]
        tree = cKDTree(tp.astype(np.float32)) 
        layers[layer] = {"idx": idxs, "tp": tp, "adc": adc, "tree": tree}

    return layers


# Find local ADC maximums

In [16]:
def is_local_max(layer_data, j):
    """
    8-neighborhood local maximum in (timebin, pad), same layer:
    neighbors are |dt|<=1, |dp|<=1 (excluding itself)
    """
    tp   = layer_data["tp"]
    adc  = layer_data["adc"]
    tree = layer_data["tree"]

    a0 = int(adc[j])


    t0, p0 = tp[j]
    
    # radius that fully contains the 3x3 box
    r = np.sqrt(2.0)
    cand = tree.query_ball_point([t0, p0], r=r)

    for k in cand:
        if k == j:
            continue

        t, p = tp[k]
        if abs(t - t0) <= 1 and abs(p - p0) <= 1:
            if adc[k] >= a0:   # STRICT local max
                return False
    #print(f"Found local max at (t={t0}, p={p0}) with adc={a0}")
    return True



def find_seeds(layers):
    """
    Returns list of seeds as tuples: (layer, j_in_layer)
    """
    seeds = []
    for layer, ld in layers.items():
        M = ld["tp"].shape[0]
        for j in range(M):
            if is_local_max(ld, j):
                seeds.append((layer, j))
    return seeds


In [17]:
def query_box_in_layer(layer_data, t0, p0, dt, dp):
    tp   = layer_data["tp"]   # int32
    tree = layer_data["tree"]

    t0 = int(t0); p0 = int(p0)
    r = float((dt*dt + dp*dp) ** 0.5)
    cand = tree.query_ball_point([float(t0), float(p0)], r=r)

    out = []
    for j in cand:
        t = int(tp[j, 0]); p = int(tp[j, 1])
        if abs(t - t0) <= dt and abs(p - p0) <= dp:
            out.append(j)
    return out

# Chaining

In [18]:

def pick_best_candidate(layer_data, cand_js, t0, p0):
    tp  = layer_data["tp"]   # int32
    adc = layer_data["adc"]

    t0 = int(t0); p0 = int(p0)

    best = None
    best_key = None
    for j in cand_js:
        t = int(tp[j, 0]); p = int(tp[j, 1])
        dist2 = (t - t0)*(t - t0) + (p - p0)*(p - p0)
        key = (int(adc[j]), -dist2)
        if best is None or key > best_key:
            best = j
            best_key = key
    return best


In [19]:
def find_seeds_sorted(layers):
    seeds = []
    for layer, ld in layers.items():
        M = ld["tp"].shape[0]
        for j in range(M):
            if is_local_max(ld, j):
                seeds.append((layer, j, int(ld["adc"][j])))

    # highest ADC first
    seeds.sort(key=lambda x: x[2], reverse=True)
    return seeds


# Find horizontal chains

In [20]:
import numpy as np
from collections import defaultdict, deque
from scipy.spatial import cKDTree

def _order_chain_in_layer(layer_data, chain_seed_js):
    """
    Order a set of seed indices (j in this layer) into a 'nice' polyline order.
    Uses PCA-like 1D projection when possible; falls back to sorting by (t,p).
    """
    tp = layer_data["tp"]  # int32, shape (M,2)
    pts = np.asarray([tp[j] for j in chain_seed_js], dtype=np.float32)  # Nx2

    if len(chain_seed_js) <= 2:
        # stable ordering
        order = np.lexsort((pts[:, 1], pts[:, 0]))  # sort by t then pad
        return [chain_seed_js[i] for i in order]

    # PCA direction = first right-singular vector of centered coords
    c = pts.mean(axis=0, keepdims=True)
    X = pts - c
    # SVD on 2D: X = U S Vt
    _, _, vt = np.linalg.svd(X, full_matrices=False)
    direction = vt[0]  # 2-vector

    s = X @ direction  # projection coordinate
    order = np.argsort(s)
    return [chain_seed_js[i] for i in order]

In [21]:
def chain_avg_dp_dt_between_maxima(chain, layers, seed_set):
    """
    Returns (avg_dp, avg_dt, n_maxima) using absolute dp/dt
    between consecutive maxima in the given chain order.
    """
    maxima = [node for node in chain if node in seed_set]
    if len(maxima) < 2:
        return None, None, len(maxima)

    dp_diffs = []
    dt_diffs = []
    for (ly1, j1), (ly2, j2) in zip(maxima, maxima[1:]):
        t1, p1 = layers[int(ly1)]["tp"][int(j1)]
        t2, p2 = layers[int(ly2)]["tp"][int(j2)]
        dp_diffs.append(abs(int(p2) - int(p1)))
        dt_diffs.append(abs(int(t2) - int(t1)))

    return float(np.mean(dp_diffs)), float(np.mean(dt_diffs)), len(maxima)


In [22]:
from collections import deque

def build_horizontal_cluster_allhits_from_seed(layers, seed_layer, seed_j, used_global,
                                               dt=2, dp=1):
    """
    Flood-fill in ONE layer from a seed, collecting ALL connected hits (same layer),
    using |dt|<=dt, |dp|<=dp.

    Marks hits as used during the fill, but returns the list of global indices it claimed
    so caller can UNDO if the cluster is rejected by quality cuts.
    """
    layer = int(seed_layer)
    ld = layers.get(layer)
    if ld is None:
        return [], []

    seed_j = int(seed_j)
    gi_seed = int(ld["idx"][seed_j])
    if gi_seed in used_global:
        return [], []

    q = deque([seed_j])
    visited_local = set([seed_j])

    chain_js = []
    consumed_gis = []

    while q:
        j = int(q.popleft())
        gi = int(ld["idx"][j])

        # if already used by some earlier accepted chain, don't take it
        if gi in used_global:
            continue

        # claim it
        used_global.add(gi)
        consumed_gis.append(gi)
        chain_js.append(j)

        t0 = int(ld["tp"][j, 0])
        p0 = int(ld["tp"][j, 1])

        neigh = query_box_in_layer(ld, t0, p0, dt=dt, dp=dp)
        for nj in neigh:
            nj = int(nj)
            if nj in visited_local:
                continue
            visited_local.add(nj)
            q.append(nj)

    chain = [(layer, j) for j in chain_js]
    return chain, consumed_gis


In [23]:
def find_horizontal_chains_allhits(layers, seeds_sorted, used_global,
                                   dt=2, dp=1,
                                   min_hits=3,
                                   min_pad_span=5,      # <-- require (pmax - pmin) > 5
                                   order_for_drawing=True):
    """
    seeds_sorted: list of (layer, j, adc) sorted by adc desc
    Builds horizontal clusters; accepts only if:
      - len(cluster) >= min_hits
      - pad span (pmax - pmin) > min_pad_span
    If rejected: UNDO used_global claims for that cluster.
    """
    horizontal_chains = []

    for (layer, j, adc) in seeds_sorted:
        chain, consumed_gis = build_horizontal_cluster_allhits_from_seed(
            layers, layer, j, used_global, dt=dt, dp=dp
        )
        if not chain:
            continue

        ly = int(chain[0][0])
        ld = layers[ly]
        js = [jj for (_, jj) in chain]

        # compute pad span
        pads = [int(ld["tp"][jj, 1]) for jj in js]
        pad_span = (max(pads) - min(pads)) if pads else 0

        # acceptance cuts
        if len(js) < min_hits or pad_span <= min_pad_span:
            # rollback: free hits for vertical iteration / other chains
            for gi in consumed_gis:
                used_global.discard(int(gi))
            continue

        if order_for_drawing:
            js_ord = _order_chain_in_layer(ld, js)
            chain = [(ly, int(jj)) for jj in js_ord]

        horizontal_chains.append(chain)

    return horizontal_chains


In [24]:
'''


def find_one_layer_seed_chains(layers, seeds, dt_chain=2, dp_chain=1, min_size=2):
    """
    Cluster ONLY local-max seeds within the SAME layer using a box window:
      |dt| <= dt_chain and |dp| <= dp_chain.

    Returns:
      chains: list of chains, each chain is list of (layer, j_in_layer) ordered for drawing
      used_gi_from_chains: set of global indices (into pts_arr[key]) for hits in those chains
    """
    seeds_by_layer = defaultdict(list)
    for (layer, j) in seeds:
        seeds_by_layer[int(layer)].append(int(j))

    chains = []
    used_gi = set()

    # for each layer, build KDTree on seed coordinates ONLY
    for layer, seed_js in seeds_by_layer.items():
        ld = layers[layer]
        tp_all = ld["tp"]  # all hits in layer

        if len(seed_js) == 0:
            continue

        seed_js = np.asarray(seed_js, dtype=np.int32)
        seed_tp = tp_all[seed_js].astype(np.float32)  # Nx2

        tree = cKDTree(seed_tp)

        # adjacency among seeds in this layer
        # radius that covers the dt/dp box
        r = float(np.sqrt(dt_chain*dt_chain + dp_chain*dp_chain))

        visited = np.zeros(len(seed_js), dtype=np.uint8)

        for i in range(len(seed_js)):
            if visited[i]:
                continue

            # BFS for connected component
            q = deque([i])
            visited[i] = 1
            comp = [i]

            while q:
                u = q.popleft()
                t0, p0 = seed_tp[u]

                cand = tree.query_ball_point([t0, p0], r=r)
                for v in cand:
                    if visited[v]:
                        continue
                    t1, p1 = seed_tp[v]
                    if abs(int(t1) - int(t0)) <= dt_chain and abs(int(p1) - int(p0)) <= dp_chain:
                        visited[v] = 1
                        q.append(v)
                        comp.append(v)

            # convert component indices -> j_in_layer list
            comp_seed_js = [int(seed_js[k]) for k in comp]

            # keep as a "chain" only if >= min_size (you can set min_size=1 if you want singles too)
            if len(comp_seed_js) >= min_size:
                ordered_js = _order_chain_in_layer(ld, comp_seed_js)
                chain = [(layer, j) for j in ordered_js]
                chains.append(chain)

                # mark their GLOBAL indices so your next iteration can skip them
                for j in ordered_js:
                    gi = int(ld["idx"][j])  # global index into pts_arr[key]
                    used_gi.add(gi)

    return chains, used_gi
'''

'\n\n\ndef find_one_layer_seed_chains(layers, seeds, dt_chain=2, dp_chain=1, min_size=2):\n    """\n    Cluster ONLY local-max seeds within the SAME layer using a box window:\n      |dt| <= dt_chain and |dp| <= dp_chain.\n\n    Returns:\n      chains: list of chains, each chain is list of (layer, j_in_layer) ordered for drawing\n      used_gi_from_chains: set of global indices (into pts_arr[key]) for hits in those chains\n    """\n    seeds_by_layer = defaultdict(list)\n    for (layer, j) in seeds:\n        seeds_by_layer[int(layer)].append(int(j))\n\n    chains = []\n    used_gi = set()\n\n    # for each layer, build KDTree on seed coordinates ONLY\n    for layer, seed_js in seeds_by_layer.items():\n        ld = layers[layer]\n        tp_all = ld["tp"]  # all hits in layer\n\n        if len(seed_js) == 0:\n            continue\n\n        seed_js = np.asarray(seed_js, dtype=np.int32)\n        seed_tp = tp_all[seed_js].astype(np.float32)  # Nx2\n\n        tree = cKDTree(seed_tp)\n\n    

# Build Vertical chains

In [25]:
'''def build_chain_from_seed(layers, seed_layer, seed_j,
                          dp_link=2, dt_link=5,
                          dp_sup=2, dt_sup=5,
                          layer_step=1,
                          stop_at_layer=None):
    """
    Returns:
      chain_main: list of (layer, j_in_layer)
      chain_support: list of (layer, j_in_layer)   # neighbors around each main hit (incl. itself if in window)
    """
    chain_main = []
    chain_support = []

    cur_layer = seed_layer
    cur_j = seed_j

    while True:
        ld = layers.get(cur_layer)
        if ld is None:
            break

        # add main
        chain_main.append((cur_layer, cur_j))

        # add support hits around this main hit in same layer
        t0, p0 = ld["tp"][cur_j]
        sup = query_box_in_layer(ld, t0, p0, dt_sup, dp_sup)
        chain_support.extend([(cur_layer, j) for j in sup])

        # stop if requested
        if stop_at_layer is not None and cur_layer >= stop_at_layer:
            break

        # move to next layer
        next_layer = cur_layer + layer_step
        ld2 = layers.get(next_layer)
        if ld2 is None:
            break

        cand = query_box_in_layer(ld2, t0, p0, dt_link, dp_link)
        if not cand:
            break

        next_j = pick_best_candidate(ld2, cand, t0, p0)
        cur_layer, cur_j = next_layer, next_j

    return chain_main, chain_support
'''

'def build_chain_from_seed(layers, seed_layer, seed_j,\n                          dp_link=2, dt_link=5,\n                          dp_sup=2, dt_sup=5,\n                          layer_step=1,\n                          stop_at_layer=None):\n    """\n    Returns:\n      chain_main: list of (layer, j_in_layer)\n      chain_support: list of (layer, j_in_layer)   # neighbors around each main hit (incl. itself if in window)\n    """\n    chain_main = []\n    chain_support = []\n\n    cur_layer = seed_layer\n    cur_j = seed_j\n\n    while True:\n        ld = layers.get(cur_layer)\n        if ld is None:\n            break\n\n        # add main\n        chain_main.append((cur_layer, cur_j))\n\n        # add support hits around this main hit in same layer\n        t0, p0 = ld["tp"][cur_j]\n        sup = query_box_in_layer(ld, t0, p0, dt_sup, dp_sup)\n        chain_support.extend([(cur_layer, j) for j in sup])\n\n        # stop if requested\n        if stop_at_layer is not None and cur_layer >

In [26]:
def build_chain_from_seed_unique(layers, seed_layer, seed_j, used_global,
                                 dp_link=2, dt_link=5,
                                 dp_sup=2, dt_sup=5,
                                 layer_step=1,
                                 mark_support_as_used=False):
    chain_main = []
    chain_support = []

    cur_layer, cur_j = int(seed_layer), int(seed_j)

    # If the seed hit is already used, don't "break" (which looks like failure),
    # just return empty so caller can skip cleanly.
    ld0 = layers.get(cur_layer)
    if ld0 is None:
        return chain_main, chain_support
    gi0 = int(ld0["idx"][cur_j])
    if gi0 in used_global:
        return chain_main, chain_support

    while True:
        ld = layers.get(cur_layer)
        if ld is None:
            break

        gi = int(ld["idx"][cur_j])
        if gi in used_global:
            break

        # add main and mark used
        chain_main.append((cur_layer, cur_j))
        used_global.add(gi)

        # integer anchor
        t0 = int(ld["tp"][cur_j, 0])
        p0 = int(ld["tp"][cur_j, 1])

        # support in same layer
        sup_js = query_box_in_layer(ld, t0, p0, dt_sup, dp_sup)
        for sj in sup_js:
            gi_s = int(ld["idx"][sj])
            if gi_s in used_global:
                continue
            chain_support.append((cur_layer, sj))
            if mark_support_as_used:
                used_global.add(gi_s)

        # step to next layer
        next_layer = cur_layer + layer_step
        ld2 = layers.get(next_layer)
        if ld2 is None:
            break

        cand = query_box_in_layer(ld2, t0, p0, dt_link, dp_link)
        if not cand:
            break

        # pick best UNUSED candidate: max ADC then closest (integer dist2)
        best = None
        best_key = None
        for j2 in cand:
            gi2 = int(ld2["idx"][j2])
            if gi2 in used_global:
                continue
            t2 = int(ld2["tp"][j2, 0])
            p2 = int(ld2["tp"][j2, 1])
            dist2 = (t2 - t0)*(t2 - t0) + (p2 - p0)*(p2 - p0)
            key = (int(ld2["adc"][j2]), -dist2)
            if best is None or key > best_key:
                best = j2
                best_key = key

        if best is None:
            break

        cur_layer, cur_j = next_layer, best

    return chain_main, chain_support


In [27]:
def dump_chain(key, chain_main, chain_support, layers, pts_arr, payload, max_lines=200):
    print(f"\n=== CHAIN key={key} main_hits={len(chain_main)} support_hits={len(chain_support)} ===")

    def print_hit(layer, j):
        gi = int(layers[layer]["idx"][j])  # global index
        tbin, pad, layer0 = pts_arr[key][gi]
        adc, entry = payload[key][gi]
        print(f"  L={int(layer0):2d}  t={int(tbin):3d}  pad={int(pad):4d}  adc={int(adc):5d}  entry={entry}")

    print("Main hits:")
    for (layer, j) in chain_main[:max_lines]:
        print_hit(layer, j)

    # If you want to see supports too:
    print("Support hits:")
    for (layer, j) in chain_support[:max_lines]:
        print_hit(layer, j)


In [28]:
key = (0, 0, 0)
layers = build_layer_indices_and_trees(key, pts_arr, payload)

# Better to sort by ADC so strongest maxima "claims" the horizontal cluster first
seeds_sorted = find_seeds_sorted(layers)   # (layer, j, adc)
print("Seeds found:", len(seeds_sorted))

used_global = set()

seed_set = set((int(ly), int(j)) for (ly, j, adc) in seeds_sorted)

# ---- 1st iteration: horizontal chains (same layer) INCLUDING ALL hits ----
horizontal_chains = find_horizontal_chains_allhits(
    layers, seeds_sorted, used_global,
    dt=2, dp=1,
    min_hits=3,
    min_pad_span=5,       # <-- >5 pads
    order_for_drawing=True
)

horizontal_chain_avg_dpdts = []
for chain in horizontal_chains:
    avg_dp, avg_dt, n_max = chain_avg_dp_dt_between_maxima(chain, layers, seed_set)
    horizontal_chain_avg_dpdts.append((avg_dp, avg_dt, n_max))


# ---- remaining seeds for 2nd iteration (vertical chains) ----
seeds_remaining = []
for (ly, j, adc) in seeds_sorted:
    gi = int(layers[int(ly)]["idx"][int(j)])
    if gi not in used_global:
        seeds_remaining.append((int(ly), int(j)))

# ---- 2nd iteration: vertical chains over consecutive layers ----
vertical_chain_avg_dpdts = []
for (seed_layer, seed_j) in seeds_remaining[:10]:
    chain_main, chain_support = build_chain_from_seed_unique(
        layers, seed_layer, seed_j, used_global,
        dp_link=2, dt_link=5,
        dp_sup=2, dt_sup=5,
        layer_step=1
    )
    avg_dp, avg_dt, n_max = chain_avg_dp_dt_between_maxima(chain_main, layers, seed_set)
    vertical_chain_avg_dpdts.append((avg_dp, avg_dt, n_max))
    dump_chain(key, chain_main, chain_support, layers, pts_arr, payload)


Seeds found: 644

=== CHAIN key=(0, 0, 0) main_hits=1 support_hits=12 ===
Main hits:
  L=22  t=196  pad=  11  adc=  955  entry=33024
Support hits:
  L=22  t=192  pad=   9  adc=  317  entry=33000
  L=22  t=193  pad=   9  adc=   87  entry=33001
  L=22  t=192  pad=  10  adc=  103  entry=33013
  L=22  t=191  pad=  10  adc=   97  entry=33012
  L=22  t=196  pad=  10  adc=  275  entry=33016
  L=22  t=195  pad=  10  adc=  208  entry=33015
  L=22  t=195  pad=  11  adc=  678  entry=33023
  L=22  t=195  pad=  12  adc=  274  entry=33030
  L=22  t=196  pad=  12  adc=  432  entry=33031
  L=22  t=197  pad=  10  adc=   73  entry=33017
  L=22  t=197  pad=  11  adc=  248  entry=33025
  L=22  t=197  pad=  12  adc=  104  entry=33032

=== CHAIN key=(0, 0, 0) main_hits=1 support_hits=10 ===
Main hits:
  L=21  t=219  pad=  78  adc=  952  entry=31855
Support hits:
  L=21  t=218  pad=  80  adc=   79  entry=31860
  L=21  t=218  pad=  78  adc=  175  entry=31854
  L=21  t=221  pad=  76  adc=  352  entry=31852
  L

In [29]:
'''key = (0, 0, 0)
layers = build_layer_indices_and_trees(key, pts_arr, payload)

seeds = find_seeds(layers)  # tune adc_min
print("Seeds found:", len(seeds))


used_global = set()

layers = build_layer_indices_and_trees(key, pts_arr, payload)
seeds  = find_seeds(layers)

# ---- 1st iteration: cluster seeds within SAME layer (dt=2, dp=1) ----
one_layer_chains, used_gi_one_layer = find_one_layer_seed_chains(
    layers, seeds,
    dt_chain=2, dp_chain=1,
    min_size=2   # only real multi-hit chains
)

# remove them for 2nd iteration (consecutive-layer chains)
used_global |= used_gi_one_layer

# keep only remaining seeds (not removed)
seeds_remaining = []
for (ly, j) in seeds:
    gi = int(layers[int(ly)]["idx"][int(j)])
    if gi not in used_global:
        seeds_remaining.append((int(ly), int(j)))


# build chains (example: first 10 seeds)
for s in seeds[:10]:
    seed_layer, seed_j = s
'''
'''chain_main, chain_support = build_chain_from_seed(
    layers, seed_layer, seed_j,
    dp_link=2, dt_link=5,
    dp_sup=2, dt_sup=5,
    layer_step=1
)'''
'''
    chain_main, chain_support = build_chain_from_seed_unique(
        layers, seed_layer, seed_j,used_global,
        dp_link=2, dt_link=5,
        dp_sup=2, dt_sup=5,
        layer_step=1
    )
    dump_chain(key, chain_main, chain_support, layers, pts_arr, payload)
'''

'\n    chain_main, chain_support = build_chain_from_seed_unique(\n        layers, seed_layer, seed_j,used_global,\n        dp_link=2, dt_link=5,\n        dp_sup=2, dt_sup=5,\n        layer_step=1\n    )\n    dump_chain(key, chain_main, chain_support, layers, pts_arr, payload)\n'

# Drawing

In [30]:
def draw_chain_3d(chain_main, key, layers, pts_arr, color, width=2):
    """
    chain_main: list of (layer, j_in_layer) in order
    """
    n = len(chain_main)
    if n < 2:
        return None

    pl = root.TPolyLine3D(n)
    pl.SetLineColor(color)
    pl.SetLineWidth(width)

    for i, (layer, j) in enumerate(chain_main):
        gi = layers[layer]["idx"][j]  # global index
        tbin, pad, layer0 = pts_arr[key][gi]
        #print(f"Chain point {i}: layer={layer0}, tbin={tbin}, pad={pad}")
        pl.SetPoint(i, float(tbin), float(pad), float(layer0))

    pl.Draw("same")
    return pl

CHAIN_COLORS = [
    root.kRed + 1,
    root.kAzure + 2,
    root.kGreen + 2,
    root.kMagenta + 1,
    root.kOrange + 7,
    root.kCyan + 2,
    root.kViolet,
    root.kPink + 9,
]


In [31]:
def draw_local_maxima_3d(seeds, key, layers, pts_arr, color, mstyle=20, msize=1.2):
    """
    seeds: list of (layer, j_in_layer)
    Draw as TPolyMarker3D at (tbin, pad, layer)
    """
    n = len(seeds)
    if n == 0:
        return None

    pm = root.TPolyMarker3D(n)
    pm.SetMarkerColor(color)
    pm.SetMarkerStyle(mstyle)
    pm.SetMarkerSize(msize)

    for i, (layer, j) in enumerate(seeds):
        gi = int(layers[layer]["idx"][j])  # global index in pts_arr[key]
        tbin, pad, layer0 = pts_arr[key][gi]
        pm.SetPoint(i, float(tbin), float(pad), float(layer0)+0.5)

    pm.Draw("same")   # important: draw on same canvas
    return pm


In [32]:
'''draw_sector = 0
draw_side   = 0

canvases = []
drawn = {}          # hist refs
drawn_chains = {}   # IMPORTANT: keep line refs

for imod in range(3):
    c = root.TCanvas(
        f"c_sec{draw_sector}_s{draw_side}_mod{imod}",
        f"Sector {draw_sector} Side {draw_side} Module {imod}",
        1500, 1000
    )
    c.cd()
    drawn_seeds = {} 
    key = (draw_sector, imod, draw_side)

    if key in hists:
        h3 = hists[key]
\
        h3.SetTitle(
            f"3D ADC; timebin; pad; layer "
            f"(sec {draw_sector}, side {draw_side}, mod {imod})"
        )

        h3.Draw("SCAT")
        drawn[imod] = h3
        used_global = set() 
        # ---- DRAW CHAINS ----
        layers = build_layer_indices_and_trees(key, pts_arr, payload)
        seeds  = find_seeds(layers)




        pm = draw_local_maxima_3d(
            seeds, key, layers, pts_arr,
            color=root.kRed+1,   # pick something visible
            mstyle=20,              # full circle
            msize=1.6
        )

        drawn_seeds[imod] = pm
        drawn_chains[imod] = []
        one_layer_chains, used_gi_one_layer = find_one_layer_seed_chains(
            layers, seeds,
            dt_chain=2, dp_chain=1,
            min_size=2   # only real multi-hit chains
        )

        # remove them for 2nd iteration (consecutive-layer chains)
        used_global |= used_gi_one_layer

        # keep only remaining seeds (not removed)
        seeds_remaining = []
        for (ly, j) in seeds:
            gi = int(layers[int(ly)]["idx"][int(j)])
            if gi not in used_global:
                seeds_remaining.append((int(ly), int(j)))

                # draw one-layer chains first (thin)
        for ic, chain in enumerate(one_layer_chains):
            color = CHAIN_COLORS[ic % len(CHAIN_COLORS)]
            pl = draw_chain_3d(chain, key, layers, pts_arr, color=color, width=3)
            if pl:
                drawn_chains[imod].append(pl)

        for ic, (seed_layer, seed_j) in enumerate(seeds):

            chain_main, _ = build_chain_from_seed_unique(
                layers,
                seed_layer,
                seed_j,
                used_global,
                dp_link=3,
                dt_link=6
            )


            if len(chain_main) < 5:
                continue  # too short, skip

            color = CHAIN_COLORS[ic % len(CHAIN_COLORS)]
            pl = draw_chain_3d(chain_main, key, layers, pts_arr,
                               color=color, width=6)
            if pl:
                drawn_chains[imod].append(pl)

    c.Update()
    canvases.append(c)

for c in canvases:
    c.Draw()


'''

'draw_sector = 0\ndraw_side   = 0\n\ncanvases = []\ndrawn = {}          # hist refs\ndrawn_chains = {}   # IMPORTANT: keep line refs\n\nfor imod in range(3):\n    c = root.TCanvas(\n        f"c_sec{draw_sector}_s{draw_side}_mod{imod}",\n        f"Sector {draw_sector} Side {draw_side} Module {imod}",\n        1500, 1000\n    )\n    c.cd()\n    drawn_seeds = {} \n    key = (draw_sector, imod, draw_side)\n\n    if key in hists:\n        h3 = hists[key]\n        h3.SetTitle(\n            f"3D ADC; timebin; pad; layer "\n            f"(sec {draw_sector}, side {draw_side}, mod {imod})"\n        )\n\n        h3.Draw("SCAT")\n        drawn[imod] = h3\n        used_global = set() \n        # ---- DRAW CHAINS ----\n        layers = build_layer_indices_and_trees(key, pts_arr, payload)\n        seeds  = find_seeds(layers)\n\n\n\n\n        pm = draw_local_maxima_3d(\n            seeds, key, layers, pts_arr,\n            color=root.kRed+1,   # pick something visible\n            mstyle=20,          

In [36]:
draw_sector = 0
draw_side   = 0

canvases = []
drawn = {}          # hist refs
drawn_chains = {}   # IMPORTANT: keep line refs
chain_avg_dpdts = {}
drawn_seeds  = {}   # keep marker refs too

for imod in range(3):
    c = root.TCanvas(
        f"c_sec{draw_sector}_s{draw_side}_mod{imod}",
        f"Sector {draw_sector} Side {draw_side} Module {imod}",
        1500, 1000
    )
    c.cd()

    key = (draw_sector, imod, draw_side)

    if key in hists:
        h3 = hists[key]
        h3.SetTitle(
            f"3D ADC; timebin; pad; layer "
            f"(sec {draw_sector}, side {draw_side}, mod {imod})"
        )
        h3.Draw("SCAT")
        drawn[imod] = h3

        # ---- build per-key structures ----
        layers = build_layer_indices_and_trees(key, pts_arr, payload)

        # IMPORTANT: sort seeds by ADC so strongest maxima "claims" clusters first
        seeds_sorted = find_seeds_sorted(layers)  # list of (layer, j, adc)
        seeds_for_markers = [(ly, j) for (ly, j, adc) in seeds_sorted]

        used_global = set()
        seed_set = set((int(ly), int(j)) for (ly, j, adc) in seeds_sorted)

        # ---- draw local maxima markers ----
        pm = draw_local_maxima_3d(
            seeds_for_markers, key, layers, pts_arr,
            color=root.kRed + 1,
            mstyle=20,
            msize=1.6
        )
        drawn_seeds[imod] = pm

        drawn_chains[imod] = []

        # ============================================================
        # 1st iteration: HORIZONTAL (same-layer) CHAINS INCLUDING ALL HITS
        # dp=±1, dt=±2
        # This FUNCTION MARKS used_global internally (consumes all hits in horizontals)
        # ============================================================
        horizontal_chains = find_horizontal_chains_allhits(
            layers, seeds_sorted, used_global,
            dt=2, dp=1,
            min_hits=3,
            min_pad_span=5,       # <-- >5 pads
            order_for_drawing=True
        )

        horizontal_chain_avg_dpdts = []
        for chain in horizontal_chains:
            avg_dp, avg_dt, n_max = chain_avg_dp_dt_between_maxima(chain, layers, seed_set)
            horizontal_chain_avg_dpdts.append((avg_dp, avg_dt, n_max))

        # draw horizontal chains first (thin)
        for ic, chain in enumerate(horizontal_chains):
            color = CHAIN_COLORS[ic % len(CHAIN_COLORS)]
            pl = draw_chain_3d(chain, key, layers, pts_arr, color=color, width=3)
            if pl:
                drawn_chains[imod].append(pl)

        # ============================================================
        # 2nd iteration: VERTICAL chains in consecutive layers
        vertical_chain_avg_dpdts = []
        # Use only seeds not already consumed by horizontal clustering
        # ============================================================
        seeds_remaining = []
        for (ly, j, adc) in seeds_sorted:
            gi = int(layers[int(ly)]["idx"][int(j)])
            if gi not in used_global:
                seeds_remaining.append((int(ly), int(j)))

        for ic, (seed_layer, seed_j) in enumerate(seeds_remaining):
            chain_main, _ = build_chain_from_seed_unique(
                layers,
                seed_layer,
                seed_j,
                used_global,
                dp_link=3,
                dt_link=6,
                dp_sup=2,
                dt_sup=5,
                layer_step=1
            )

            avg_dp, avg_dt, n_max = chain_avg_dp_dt_between_maxima(chain_main, layers, seed_set)
            vertical_chain_avg_dpdts.append((avg_dp, avg_dt, n_max))

            if len(chain_main) < 5:
                continue

            color = CHAIN_COLORS[ic % len(CHAIN_COLORS)]
            pl = draw_chain_3d(chain_main, key, layers, pts_arr, color=color, width=6)
            if pl:
                drawn_chains[imod].append(pl)

        chain_avg_dpdts[imod] = {
            "horizontal": horizontal_chain_avg_dpdts,
            "vertical": vertical_chain_avg_dpdts,
        }

    c.Update()
    canvases.append(c)

for c in canvases:
    c.Draw()
